## Import Files

In [1]:
f = open("input.txt", "r")
states = []
for line in f:
    state = [float(x) for x in line.split()]
    states.append(state)

In [2]:
f = open("input_pv_names.txt", "r")
pv_names = []
for line in f:
    pv_names.append(line[:-1])

In [3]:
f = open("output.txt", "r")
output = []
for line in f:
    output.append(float(line))

In [4]:
len(states)

489588

In [5]:
min(output)

-372.44085371520816

In [6]:
len(pv_names)

226

## Calcultate nuber of uniqe Setpoints

In [7]:
def uniqes_of_index(i):
    seen = set()
    uniqes = []
    for state in states:
        if state[i] not in seen:
            seen.add(state[i])
            uniqes.append(state[i]) # we need the list to maintain the order
    return uniqes

In [8]:
uniqes = []
for i in range(len(pv_names)):
    uniqes.append(uniqes_of_index(i))

## Pruning the dataset

we want to ignore every element with too little datapoints, 100 is chosen, every one with above 3000 also happens to be ignored due to it being not set by hand

In [9]:
numOfUniqes = []
excludeMap = []
for i in range(226):
    numOfUniqes.append([pv_names[i],len(uniqes[i])])
    if len(uniqes[i]) < 3000 and len(uniqes[i]) > 100:
        excludeMap.append(1)
    else:
        excludeMap.append(0)
numOfUniqes

[['G0SH01:outCur', 1],
 ['I0SH01:outCur', 334],
 ['I0SH02:outCur', 183],
 ['I0SH03:outCur', 193],
 ['I0SH04:outCur', 48],
 ['I0SH05:outCur', 61],
 ['I0SH06:outCur', 574],
 ['I0CH01:outCur', 1062],
 ['I1SH01:outCur', 558],
 ['I1SH02:outCur', 235],
 ['A1SH01:outCur', 463],
 ['A1SH02:outCur', 378],
 ['A1SH03:outCur', 339],
 ['A1SH04:outCur', 333],
 ['F1SH01:outCur', 358],
 ['F1SH02:outCur', 273],
 ['F1SH03:outCur', 159],
 ['F1SH04:outCur', 317],
 ['S1SH01:outCur', 370],
 ['S1SH02:outCur', 254],
 ['S1SH03:outCur', 444],
 ['S1SH04:outCur', 562],
 ['S1SH05:outCur', 426],
 ['S1SH06:outCur', 508],
 ['T1SH01:outCur', 198],
 ['T1SH02:outCur', 80],
 ['T1SH03:outCur', 114],
 ['T1SH04:outCur', 188],
 ['T1SH05:outCur', 142],
 ['E0SH01:outCur', 314],
 ['E0SH02:outCur', 209],
 ['G0SV01:outCur', 1],
 ['I0SV01:outCur', 176],
 ['I0SV02:outCur', 90],
 ['I0SV03:outCur', 190],
 ['I0SV04:outCur', 463],
 ['I0SV05:outCur', 90],
 ['I0SV06:outCur', 460],
 ['I0CV01:outCur', 2484],
 ['I1SV01:outCur', 525],
 ['A1SV

excludeMap now contains a 1 for every PV that we should keep

In [10]:
reducedStates = []
for state in states:
    redState = []
    for i in range(226):
        if excludeMap[i]:
            redState.append(state[i])
    reducedStates.append(redState)

In [11]:
reducedPvNames = []
for i in range(226):
    if excludeMap[i]:
        reducedPvNames.append(pv_names[i])
reducednumOfUniqes = []
for i in range(226):
    if excludeMap[i]:
        reducednumOfUniqes.append(numOfUniqes[i])

In [12]:
outStates = []
for i in range(len(reducedStates)):
    outStates.append([reducedStates[i], output[i]])

[[[-1.2100000000000009,
   0.0,
   0.6500000000000004,
   -2.7887500000000003,
   -0.05000000000000071,
   0.16000000000000014,
   -0.34999999999999964,
   -0.96875,
   -0.5,
   -0.5999999999999996,
   0.0,
   -0.5428125000000001,
   -0.5899999999999999,
   -0.05000000000000071,
   -0.8499999999999996,
   0.0,
   0.6500000000000004,
   0.3000000000000007,
   -0.6699999999999999,
   0.33000000000000007,
   -0.8200000000000003,
   0.0,
   0.0,
   0.0,
   0.0,
   -3.0,
   2.1500000000000004,
   -1.0362500000000008,
   0.6259374999999991,
   -0.2599999999999998,
   0.10999999999999943,
   -0.5700000000000003,
   -2.4400000000000004,
   0.10999999999999943,
   0.0,
   0.33000000000000007,
   0.0,
   0.0,
   -1.0600000000000005,
   0.47000000000000064,
   0.34999999999999964,
   -0.08000000000000007,
   -0.6199999999999992,
   0.0,
   0.0,
   0.0,
   0.0,
   -0.8699999999999992,
   -0.13781250000000078,
   -0.2400000000000002,
   0.1999999999999993,
   0.40000000000000036,
   0.0,
   0.0,
  

Our data contains the vector and coresponding output for that vector, but there are still duplicates pesssent...
For a duplictae we want to take the minimum value since we assume that the operator can set to optimal values for the excluded parameters. This is important

In [13]:
seen = set()
minima = dict()
index = dict()
result = []

i = 0

for state in outStates:
    key = tuple(state[0])
    if key not in seen:
        seen.add(key)
        minima[key] = state[1]
        index[key] = i
        result.append(state)
        i = i+1
    else:
        if state[1] < minima[key]:
            result[index[key]]= [key, state[1]]

In [14]:
len(result)

142534

In [64]:
len(reducedPvNames)

151

Also we want to make sure the maximum current is 0, exclude measurment noise resulting in a positive current

In [15]:
for i, state in enumerate(result):
    if state[1] > 0:
        result[i] = [state[0],0]

## Store the Calculated tables

In [16]:
import pickle

In [17]:
file_path = 'E0F1.pkl'
with open(file_path, 'wb') as file:
    pickle.dump(result, file)


In [18]:
file_path = 'E0F1numOfUniqes.pkl'
with open(file_path, 'wb') as file:
    pickle.dump(numOfUniqes, file)

In [19]:
file_path = 'E0F1Names.pkl'
with open(file_path, 'wb') as file:
    pickle.dump(reducedPvNames, file)

Loading them from file... 

In [20]:
result = pickle.load(open('E0F1.pkl', 'rb'))
numOfUniqes = pickle.load(open('E0F1numOfUniqes.pkl', 'rb'))
reducedPvNames = pickle.load(open('E0F1Names.pkl', 'rb'))

## Well need some indextables to speed up calls later

first all states with at least partial transmission (used as legal startion possitions)

In [57]:
index_transmison = []
for i, state in enumerate(result):
    if state[1] < -60:
        index_transmison.append(i)

In [58]:
len(index_transmison)/len(result)

0.5572003872760184

In [59]:
file_path = 'E0F1_index_transmision.pkl'
with open(file_path, 'wb') as file:
    pickle.dump(index_transmison, file)

second lists of all indexees beloning to each subsection

In [60]:
index_I0 = []
for i, name in enumerate(reducedPvNames):
    if 'I0' in name :
        index_I0.append(i)
len(index_I0)

15

In [61]:
index_I1 = []
for i, name in enumerate(reducedPvNames):
    if 'I1' in name :
        index_I1.append(i)
len(index_I1)

12

In [62]:
index_A1 = []
for i, name in enumerate(reducedPvNames):
    if 'A1' in name :
        index_A1.append(i)
len(index_A1)

19

Now lets export those

In [63]:
file_path = 'E0F1_index_transmision.pkl'
pickle.dump(index_transmison, open(file_path, 'wb'))

file_path = 'E0F1_index_I0.pkl'
pickle.dump(index_I0, open(file_path, 'wb'))

file_path = 'E0F1_index_I1.pkl'
pickle.dump(index_I1, open(file_path, 'wb'))

file_path = 'E0F1_index_A1.pkl'
pickle.dump(index_A1, open(file_path, 'wb'))

## We want to calculate some interesting Information to be used later

In [38]:
minimum = 0
minindex = 0
for i, state in enumerate(result):
    if state[1] < minimum:
        minimum = state[1]
        minindex = i
f"optimum at index {minindex} with {minimum}"

'optimum at index 40104 with -371.61877453353645'

In [66]:
def getRangeForIndex(i):
    minimum = 9999999999
    maximum = -9999999999
    for state in result:
        if state[0][i] < minimum:
            minimum = state[0][i]
        if state[0][i] > maximum:
            maximum = state[0][i]
    return [minimum, maximum]
    

In [45]:
#index list
for i, name in enumerate(reducedPvNames):
    range = getRangeForIndex(i)
    print(f"{i}: {name}                      range: {range[0]} to {range[1]}     total: {range[1]-range[0]}")

0: I0SH01:outCur                      range: -1.2759374999999995 to -1.0859     total: 0.19003749999999942
1: I0SH02:outCur                      range: -0.2544 to 0.1856     total: 0.44
2: I0SH03:outCur                      range: 0.5090625000000006 to 0.7791     total: 0.2700374999999994
3: I0SH06:outCur                      range: -3.1025 to -2.6537500000000005     total: 0.44874999999999954
4: I0CH01:outCur                      range: -1.0409375 to 0.5591     total: 1.6000375
5: I1SH01:outCur                      range: -0.2078124999999993 to 0.2578125     total: 0.4656249999999993
6: I1SH02:outCur                      range: -0.40000000000000036 to -0.23     total: 0.17000000000000035
7: A1SH01:outCur                      range: -1.0412499999999998 to -0.9091     total: 0.13214999999999977
8: A1SH02:outCur                      range: -0.5996874999999999 to -0.41     total: 0.18968749999999995
9: A1SH03:outCur                      range: -0.5999999999999996 to -0.45374999999999943  

87: I1QU01:outCur                      range: 0.2628 to 0.6028125000000006     total: 0.34001250000000066
88: I1QU02:outCur                      range: 0.7094 to 0.9094     total: 0.19999999999999996
89: A1QU01:outCur                      range: -0.3056 to 0.18406249999999957     total: 0.48966249999999956
90: A1QU02:outCur                      range: 0.0912 to 0.2044     total: 0.1132
91: A1QU03:outCur                      range: -0.3003125000000004 to -0.1803     total: 0.12001250000000044
92: A1QU04:outCur                      range: -0.0600000000000005 to 0.03     total: 0.0900000000000005
93: F0QU01:outCur                      range: 1.3383 to 1.5521875000000005     total: 0.21388750000000045
94: F0QU02:outCur                      range: -0.5746874999999996 to -0.45     total: 0.12468749999999956
95: F0QU03:outCur                      range: 1.5578125000000007 to 1.6659375     total: 0.10812499999999936
96: F1QU01:outCur                      range: 0.7896874999999994 to 1.8797    

In [73]:
index_I1_range = []
for i in index_I1:
    mini, maxi = getRangeForIndex(i)
    delta = maxi - mini
    index_I1_range.append(delta)
index_I1_range

[0.4656249999999993,
 0.17000000000000035,
 0.6524999999999999,
 0.14566250000000042,
 0.34001250000000066,
 0.19999999999999996,
 0.14499999999999957,
 0.13628749999999912,
 59.239959716796875,
 13.40057373046875,
 39.3402099609375,
 24.9005126953125]